<a href="https://colab.research.google.com/github/sanketh96/Chatbot-2.0/blob/master/NER_LSTM_Augmented.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
import pandas as pd
import numpy as np
import copy

In [0]:
!pip install kaggle


In [0]:
from googleapiclient.discovery import build
import io, os
from googleapiclient.http import MediaIoBaseDownload
from google.colab import auth
auth.authenticate_user()
drive_service = build('drive', 'v3')
results = drive_service.files().list(
        q="name = 'kaggle.json'", fields="files(id)").execute()
kaggle_api_key = results.get('files', [])
filename = "/content/.kaggle/kaggle.json"
os.makedirs(os.path.dirname(filename), exist_ok=True)

In [0]:
request = drive_service.files().get_media(fileId=kaggle_api_key[0]['id'])
fh = io.FileIO(filename, 'wb')
downloader = MediaIoBaseDownload(fh, request)
done = False
while done is False:
    status, done = downloader.next_chunk()
    print("Download %d%%." % int(status.progress() * 100))
os.chmod(filename, 600)

Download 100%.


In [0]:
!mkdir ~/.kaggle
!cp /content/.kaggle/kaggle.json ~/.kaggle/kaggle.json



mkdir: cannot create directory ‘/root/.kaggle’: File exists


In [0]:
!kaggle datasets download -d abhinavwalia95/entity-annotated-corpus

entity-annotated-corpus.zip: Skipping, found more recently modified local copy (use --force to force download)


In [0]:
!unzip entity-annotated-corpus.zip

Archive:  entity-annotated-corpus.zip
replace ner.csv? [y]es, [n]o, [A]ll, [N]one, [r]ename: n
replace ner_dataset.csv? [y]es, [n]o, [A]ll, [N]one, [r]ename: n


In [0]:
!ls

adc.json       entity-annotated-corpus.zip  ner.csv	     sample_data
augmented.csv  gdrive			    ner_dataset.csv


In [0]:
data = pd.read_csv("ner_dataset.csv", encoding="latin1").fillna(method="ffill")
data.tail(10)

Sentence #       Word  POS    Tag
1048565  Sentence: 47958     impact   NN      O
1048566  Sentence: 47958          .    .      O
1048567  Sentence: 47959     Indian   JJ  B-gpe
1048568  Sentence: 47959     forces  NNS      O
1048569  Sentence: 47959       said  VBD      O
1048570  Sentence: 47959       they  PRP      O
1048571  Sentence: 47959  responded  VBD      O
1048572  Sentence: 47959         to   TO      O
1048573  Sentence: 47959        the   DT      O
1048574  Sentence: 47959     attack   NN      O

In [0]:
data = data.rename(index=str, columns = {"Sentence #":"sentence_id", "Word":"word","Tag":"final_tag"})

In [0]:
data.head()

sentence_id           word  POS final_tag
0  Sentence: 1      Thousands  NNS         O
1  Sentence: 1             of   IN         O
2  Sentence: 1  demonstrators  NNS         O
3  Sentence: 1           have  VBP         O
4  Sentence: 1        marched  VBN         O

In [0]:
sentence_word = "Sentence: 1"
sentence_word[10:]

'1'

In [0]:
data['sentence_id'] = data['sentence_id'].apply(lambda x : x[10:])

In [0]:
data.head()

sentence_id           word  POS final_tag
0           1      Thousands  NNS         O
1           1             of   IN         O
2           1  demonstrators  NNS         O
3           1           have  VBP         O
4           1        marched  VBN         O

In [0]:
data['final_tag'].value_counts()

O        887908
B-geo     37644
B-tim     20333
B-org     20143
I-per     17251
B-per     16990
I-org     16784
B-gpe     15870
I-geo      7414
I-tim      6528
B-art       402
B-eve       308
I-art       297
I-eve       253
B-nat       201
I-gpe       198
I-nat        51
Name: final_tag, dtype: int64

In [0]:
data

sentence_id           word  POS final_tag
0                 1      Thousands  NNS         O
1                 1             of   IN         O
2                 1  demonstrators  NNS         O
3                 1           have  VBP         O
4                 1        marched  VBN         O
5                 1        through   IN         O
6                 1         London  NNP     B-geo
7                 1             to   TO         O
8                 1        protest   VB         O
9                 1            the   DT         O
10                1            war   NN         O
11                1             in   IN         O
12                1           Iraq  NNP     B-geo
13                1            and   CC         O
14                1         demand   VB         O
15                1            the   DT         O
16                1     withdrawal   NN         O
17                1             of   IN         O
18                1        British   JJ     B-gpe
19                1         troops  NNS         O
20                1           from   IN         O
21                1           that   DT         O
22                1        country   NN         O
23                1              .    .         O
24                2       Families  NNS         O
25                2             of   IN         O
26                2       soldiers  NNS         O
27                2         killed  VBN         O
28                2             in   IN         O
29                2            the   DT         O
...             ...            ...  ...       ...
1048545       47957            Two   CD         O
1048546       47957           more  JJR         O
1048547       47957         landed  VBD         O
1048548       47957             in   IN         O
1048549       47957         fields  NNS         O
1048550       47957      belonging  VBG         O
1048551       47957             to   TO         O
1048552       47957              a   DT         O
1048553       47957         nearby   JJ         O
1048554       47957        village   NN         O
1048555       47957              .    .         O
1048556       47958           They  PRP         O
1048557       47958            say  VBP         O
1048558       47958            not   RB         O
1048559       47958            all   DT         O
1048560       47958             of   IN         O
1048561       47958            the   DT         O
1048562       47958        rockets  NNS         O
1048563       47958       exploded  VBD         O
1048564       47958           upon   IN         O
1048565       47958         impact   NN         O
1048566       47958              .    .         O
1048567       47959         Indian   JJ     B-gpe
1048568       47959         forces  NNS         O
1048569       47959           said  VBD         O
1048570       47959           they  PRP         O
1048571       47959      responded  VBD         O
1048572       47959             to   TO         O
1048573       47959            the   DT         O
1048574       47959         attack   NN         O

[1048575 rows x 4 columns]

In [0]:
class SentenceGetter(object):
    
    def __init__(self, data):
        self.n_sent = 1
        self.data = data
        self.empty = False
        agg_func = lambda s: [(w, p, t) for w, p, t in zip(s["word"].values.tolist(),
                                                           s["POS"].values.tolist(),
                                                           s["final_tag"].values.tolist())]
        self.grouped = self.data.groupby("sentence_id").apply(agg_func)
        self.sentences = [s for s in self.grouped]
    
    def get_next(self):
        try:
            s = self.grouped[self.n_sent]
            self.n_sent += 1
            return s
        except:
            return None


In [0]:
data_per = data[data['final_tag'] == 'B-per'].sample(7000)
data_geo = data[data['final_tag'] == 'B-geo'].sample(3000)
data_gpe = data[data['final_tag'] == 'B-gpe'].sample(5000)
data_org = data[data['final_tag'] == 'B-org'].sample(3000)
data_tim = data[data['final_tag'] == 'B-tim'].sample(3000)
data_art = data[data['final_tag'] == 'B-art']
data_eve = data[data['final_tag'] == 'B-eve']

In [0]:
data_eve.head()

sentence_id       word   POS final_tag
4853         219       2012    CD     B-eve
4887         220      Games  NNPS     B-eve
5001         224      Games  NNPS     B-eve
5035         227       2008    CD     B-eve
5170         234  Operation   NNP     B-eve

In [0]:
sentences = list(data_per["sentence_id"]) + list(data_geo["sentence_id"]) + list(data_gpe["sentence_id"]) + list(data_org["sentence_id"]) + list(data_tim["sentence_id"]) + list(data_art["sentence_id"]) + list(data_eve["sentence_id"])

In [0]:
sentences = set(sentences)

In [0]:
len(sentences)

16863

In [0]:
data[data["sentence_id"].isin(sentences)]['sentence_id'].nunique()

16863

In [0]:
data[data["sentence_id"].isin(sentences)]

sentence_id        word  POS final_tag
83                5         The   DT         O
84                5     protest   NN         O
85                5       comes  VBZ         O
86                5          on   IN         O
87                5         the   DT         O
88                5         eve   NN         O
89                5          of   IN         O
90                5         the   DT         O
91                5      annual   JJ         O
92                5  conference   NN         O
93                5          of   IN         O
94                5     Britain  NNP     B-geo
95                5          's  POS         O
96                5      ruling  VBG         O
97                5       Labor  NNP     B-org
98                5       Party  NNP     I-org
99                5          in   IN         O
100               5         the   DT         O
101               5    southern   JJ         O
102               5     English   JJ     B-gpe
103               5     seaside   NN         O
104               5      resort   NN         O
105               5          of   IN         O
106               5    Brighton  NNP     B-geo
107               5           .    .         O
196              10     Iranian   JJ     B-gpe
197              10   officials  NNS         O
198              10         say  VBP         O
199              10        they  PRP         O
200              10      expect  VBP         O
...             ...         ...  ...       ...
1048466       47953      forces  NNS         O
1048467       47953    recently   RB         O
1048468       47953   conducted  VBD         O
1048469       47953           a   DT         O
1048470       47953     mission   NN         O
1048471       47953           .    .         O
1048521       47956      Indian   JJ     B-gpe
1048522       47956   officials  NNS         O
1048523       47956        said  VBD         O
1048524       47956          no   DT         O
1048525       47956         one   NN         O
1048526       47956         was  VBD         O
1048527       47956     injured  VBN         O
1048528       47956          in   IN         O
1048529       47956    Saturday  NNP     B-tim
1048530       47956          's  POS         O
1048531       47956    incident   NN         O
1048532       47956         but   CC         O
1048533       47956        that   IN         O
1048534       47956         two   CD         O
1048535       47956          of   IN         O
1048536       47956         the   DT         O
1048537       47956     rockets  NNS         O
1048538       47956      landed  VBD         O
1048539       47956        near   IN         O
1048540       47956           a   DT         O
1048541       47956      border   NN         O
1048542       47956    security   NN         O
1048543       47956     outpost   NN         O
1048544       47956           .    .         O

[406407 rows x 4 columns]

In [0]:
data_augment = data[data["sentence_id"].isin(sentences)]

In [0]:
data_augment

sentence_id        word  POS final_tag
83                5         The   DT         O
84                5     protest   NN         O
85                5       comes  VBZ         O
86                5          on   IN         O
87                5         the   DT         O
88                5         eve   NN         O
89                5          of   IN         O
90                5         the   DT         O
91                5      annual   JJ         O
92                5  conference   NN         O
93                5          of   IN         O
94                5     Britain  NNP     B-geo
95                5          's  POS         O
96                5      ruling  VBG         O
97                5       Labor  NNP     B-org
98                5       Party  NNP     I-org
99                5          in   IN         O
100               5         the   DT         O
101               5    southern   JJ         O
102               5     English   JJ     B-gpe
103               5     seaside   NN         O
104               5      resort   NN         O
105               5          of   IN         O
106               5    Brighton  NNP     B-geo
107               5           .    .         O
196              10     Iranian   JJ     B-gpe
197              10   officials  NNS         O
198              10         say  VBP         O
199              10        they  PRP         O
200              10      expect  VBP         O
...             ...         ...  ...       ...
1048466       47953      forces  NNS         O
1048467       47953    recently   RB         O
1048468       47953   conducted  VBD         O
1048469       47953           a   DT         O
1048470       47953     mission   NN         O
1048471       47953           .    .         O
1048521       47956      Indian   JJ     B-gpe
1048522       47956   officials  NNS         O
1048523       47956        said  VBD         O
1048524       47956          no   DT         O
1048525       47956         one   NN         O
1048526       47956         was  VBD         O
1048527       47956     injured  VBN         O
1048528       47956          in   IN         O
1048529       47956    Saturday  NNP     B-tim
1048530       47956          's  POS         O
1048531       47956    incident   NN         O
1048532       47956         but   CC         O
1048533       47956        that   IN         O
1048534       47956         two   CD         O
1048535       47956          of   IN         O
1048536       47956         the   DT         O
1048537       47956     rockets  NNS         O
1048538       47956      landed  VBD         O
1048539       47956        near   IN         O
1048540       47956           a   DT         O
1048541       47956      border   NN         O
1048542       47956    security   NN         O
1048543       47956     outpost   NN         O
1048544       47956           .    .         O

[406407 rows x 4 columns]

In [0]:
data_augment['final_tag'].value_counts()

O        323393
B-geo     16111
I-per     11546
B-per     11184
B-tim      9683
B-org      9642
B-gpe      9400
I-org      7918
I-geo      3093
I-tim      2999
B-art       402
B-eve       308
I-art       297
I-eve       253
I-gpe       117
B-nat        49
I-nat        12
Name: final_tag, dtype: int64

In [0]:
getter = SentenceGetter(data_augment)

In [0]:
replacement_dict = {
    "B-gpe":"B-GPE",
    "I-gpe":"I-GPE",
    "B-per":"B-PER",
    "I-per":"I-PER",
    "B-geo":"B-LOC",
    "I-geo":"I-LOC",
    "B-tim":"B-DT",
    "I-tim":"I-DT",
    "B-art":"B-ART",
    "I-art":"I-ART",
    "B-eve":"B-EVE",
    "I-eve":"I-EVE",
    "B-org":"B-ORG",
    "I-org":"I-ORG",
    "B-nat":"o",
    "I-nat":"o",
    "O":"o"
}

In [0]:
new_data = []
sent_count = 1
for sentence in getter.sentences:
  for word in sentence:
    data_dict = {}
    data_dict['sentence_id'] = sent_count
    data_dict['word'] = word[0]
    data_dict['POS'] = word[1]
    data_dict['final_tag'] = replacement_dict[word[2]]
    new_data.append(data_dict)
  sent_count += 1

In [0]:
new_data

[{'POS': 'JJ', 'final_tag': 'B-GPE', 'sentence_id': 1, 'word': 'Iranian'},
 {'POS': 'NNS', 'final_tag': 'o', 'sentence_id': 1, 'word': 'officials'},
 {'POS': 'VBP', 'final_tag': 'o', 'sentence_id': 1, 'word': 'say'},
 {'POS': 'PRP', 'final_tag': 'o', 'sentence_id': 1, 'word': 'they'},
 {'POS': 'VBP', 'final_tag': 'o', 'sentence_id': 1, 'word': 'expect'},
 {'POS': 'TO', 'final_tag': 'o', 'sentence_id': 1, 'word': 'to'},
 {'POS': 'VB', 'final_tag': 'o', 'sentence_id': 1, 'word': 'get'},
 {'POS': 'NN', 'final_tag': 'o', 'sentence_id': 1, 'word': 'access'},
 {'POS': 'TO', 'final_tag': 'o', 'sentence_id': 1, 'word': 'to'},
 {'POS': 'JJ', 'final_tag': 'o', 'sentence_id': 1, 'word': 'sealed'},
 {'POS': 'JJ', 'final_tag': 'o', 'sentence_id': 1, 'word': 'sensitive'},
 {'POS': 'NNS', 'final_tag': 'o', 'sentence_id': 1, 'word': 'parts'},
 {'POS': 'IN', 'final_tag': 'o', 'sentence_id': 1, 'word': 'of'},
 {'POS': 'DT', 'final_tag': 'o', 'sentence_id': 1, 'word': 'the'},
 {'POS': 'NN', 'final_tag': 

In [0]:
new_data_df = pd.DataFrame(new_data)

In [0]:
new_data_df.head()

POS final_tag  sentence_id       word
0   JJ     B-GPE            1    Iranian
1  NNS         o            1  officials
2  VBP         o            1        say
3  PRP         o            1       they
4  VBP         o            1     expect

In [0]:
url = 'https://raw.githubusercontent.com/sanketh96/NER/master/combined_data.csv?token=AOeG7lr8JKLLjigFr4t5Zbi3I8IQgeqHks5clJ-0wA%3D%3D'
data = pd.read_csv(url)

In [0]:
data.tail()

Unnamed: 0 POS  sentence_id  tag1 tag2 tag3 tag4    word final_tag
220918       86629  TO         8733  B-PP    o    o    o      to         o
220919       86630  DT         8733  B-NP    o    o    o    this         o
220920       86631  JJ         8733  I-NP    o    o    o    high         o
220921       86632  NN         8733  I-NP    o    o    o  office         o
220922       86633   .         8733     o    o    o    o       .         o

In [0]:
data.drop(columns=['Unnamed: 0'])

POS  sentence_id    tag1         tag2           tag3 tag4  \
0       NNP            0    B-NP            o              o    o   
1         :            0      NP            o              o    o   
2        NN            0    B-NP       B-URLS              o    o   
3         :            0      NP       I-URLS              o    o   
4        NN            0    B-NP       I-URLS              o    o   
5        NN            0    I-NP       I-URLS              o    o   
6        JJ            0    I-NP       I-URLS              o    o   
7        NN            0    I-NP       I-URLS              o    o   
8       NNP            0    I-NP       I-URLS              o    o   
9       NNP            0    I-NP            o              o    o   
10        :            0      NP            o              o    o   
11       CD            0    B-NP            o              o    o   
12        .            0      NP            o              o    o   
13       CD            1    B-NP            o              o    o   
14      NNP            1    I-NP            o              o    o   
15      NNP            1    I-NP       B-URLS              o    o   
16      NNP            1    I-NP       I-URLS              o    o   
17      NNS            1    I-NP       I-URLS              o    o   
18        (            1    I-NP            o              o    o   
19      NNP            1    B-NP  B-EDUCATION  B-CERTIFICATE    o   
20      SYM            1    I-NP            o              o    o   
21      NNP            2    B-NP  B-EDUCATION  B-CERTIFICATE    o   
22      NNP            2    I-NP  I-EDUCATION  I-CERTIFICATE    o   
23       NN            2    I-NP            o              o    o   
24      SYM            3       o            o              o    o   
25      NNP            3    B-NP            o              o    o   
26       RB            3  B-ADVP            o              o    o   
27      VBD            3    B-VP            o              o    o   
28       IN            3    B-PP            o              o    o   
29      NNP            3    B-NP     B-PERSON        B-GROUP    o   
...     ...          ...     ...          ...            ...  ...   
220893   NN         8731    I-NP            o              o    o   
220894  NNS         8731    I-NP            o              o    o   
220895    .         8731       o            o              o    o   
220896   DT         8732    B-NP            o              o    o   
220897   JJ         8732    I-NP            o              o    o   
220898   NN         8732    I-NP            o              o    o   
220899   MD         8732    B-VP            o              o    o   
220900   VB         8732    I-VP            o              o    o   
220901   IN         8732    B-PP            o              o    o   
220902   DT         8732    B-NP            o              o    o   
220903  VBG         8732    I-NP            o              o    o   
220904   NN         8732    I-NP            o              o    o   
220905    .         8732       o            o              o    o   
220906  PRP         8733    B-NP            o              o    o   
220907   MD         8733    B-VP            o              o    o   
220908   VB         8733    I-VP            o              o    o   
220909   TO         8733    I-VP            o              o    o   
220910   VB         8733    I-VP            o              o    o   
220911   DT         8733    B-NP            o              o    o   
220912  NNS         8733    I-NP            o              o    o   
220913   IN         8733    B-PP            o              o    o   
220914  NNP         8733    B-NP     B-NATION              o    o   
220915   IN         8733    B-PP            o              o    o   
220916  VBG         8733    B-VP            o              o    o   
220917  PRP         8733    B-NP            o              o    o   
220918   TO         8733    B-PP            o              o    o   
220919

In [0]:
data['final_tag'].value_counts()

o        193632
B-PER      4614
B-LOC      3524
I-PER      3375
B-DT       2842
B-NUM      2834
I-ORG      2094
B-ORG      1662
B-GPE      1360
I-LOC      1339
I-NUM      1043
I-DT        825
I-GPE       767
I-EVE       458
B-EVE       326
B-ART       141
I-ART        87
Name: final_tag, dtype: int64

In [0]:
data = data[['POS', 'final_tag', 'sentence_id', 'word']]

In [0]:
data.tail()

POS final_tag  sentence_id    word
220918  TO         o         8733      to
220919  DT         o         8733    this
220920  JJ         o         8733    high
220921  NN         o         8733  office
220922   .         o         8733       .

In [0]:
data.dtypes

POS            object
final_tag      object
sentence_id     int64
word           object
dtype: object

In [0]:
new_data_df.dtypes

POS            object
final_tag      object
sentence_id     int64
word           object
dtype: object

In [0]:
max_sentences = data['sentence_id'].max()
max_sentences

8733

In [0]:
new_data_df['sentence_id'] = new_data_df['sentence_id'].apply(lambda x : x + max_sentences)

In [0]:
new_data_df.head()

POS final_tag  sentence_id       word
0   JJ     B-GPE         8734    Iranian
1  NNS         o         8734  officials
2  VBP         o         8734        say
3  PRP         o         8734       they
4  VBP         o         8734     expect

In [0]:
augmented_data = pd.concat([data, new_data_df])
augmented_data.tail()

POS final_tag  sentence_id             word
406402   NN         o        25596    post-election
406403    ,         o        25596                ,
406404   JJ         o        25596  anti-government
406405  NNS         o        25596   demonstrations
406406    .         o        25596                .

In [0]:
data = augmented_data

In [0]:
data['final_tag'].value_counts()

o        517086
B-LOC     19635
B-PER     15798
I-PER     14921
B-DT      12525
B-ORG     11304
B-GPE     10760
I-ORG     10012
I-LOC      4432
I-DT       3824
B-NUM      2834
I-NUM      1043
I-GPE       884
I-EVE       711
B-EVE       634
B-ART       543
I-ART       384
Name: final_tag, dtype: int64

In [0]:
data.to_csv('augmented.csv')

In [0]:
len(data['final_tag'].isna()) == len(data) # no missing tags

True

In [0]:
len(data['word'].isna()) == len(data) # no missing words

True

In [0]:
words = list(data['word'].values)

In [0]:
len(set(words))

32708

In [0]:
[word for word in words if not(word.isalnum())]

AttributeError: ignored

In [0]:
len([word for word in words if str(word).isalnum()])

544534

In [0]:
n_words = len(words)

In [0]:
class SentenceGetter(object):
    
    def __init__(self, data):
        self.n_sent = 1
        self.data = data
        self.empty = False
        agg_func = lambda s: [(w, p, t) for w, p, t in zip(s["word"].values.tolist(),
                                                           s["POS"].values.tolist(),
                                                           s["final_tag"].values.tolist())]
        self.grouped = self.data.groupby("sentence_id").apply(agg_func)
        self.sentences = [s for s in self.grouped]
    
    def get_next(self):
        try:
            s = self.grouped[self.n_sent]
            self.n_sent += 1
            return s
        except:
            return None


In [0]:
getter = SentenceGetter(data)

In [0]:
getter.sentences

[[('URL', 'NNP', 'o'),
  (';', ':', 'o'),
  ('http', 'NN', 'o'),
  (':', ':', 'o'),
  ('/', 'NN', 'o'),
  ('/', 'NN', 'o'),
  ('www.indiapost.gov.in', 'JJ', 'o'),
  ('/', 'NN', 'o'),
  ('NSC.aspx', 'NNP', 'o'),
  ('Time', 'NNP', 'o'),
  (':', ':', 'o'),
  ('3', 'CD', 'o'),
  ('.', '.', 'o')],
 [('30', 'CD', 'o'),
  ('P.M', 'NNP', 'o'),
  ('National', 'NNP', 'o'),
  ('Savings', 'NNP', 'o'),
  ('Certificates', 'NNS', 'o'),
  ('(', '(', 'o'),
  ('NSC', 'NNP', 'o'),
  (')', 'SYM', 'o')],
 [('NSC', 'NNP', 'o'), ('VIII', 'NNP', 'o'), ('Issue', 'NN', 'o')],
 [('*', 'SYM', 'o'),
  ('Scheme', 'NNP', 'o'),
  ('specially', 'RB', 'o'),
  ('designed', 'VBD', 'o'),
  ('for', 'IN', 'o'),
  ('Government', 'NNP', 'B-PER'),
  ('employees', 'NNS', 'I-PER'),
  (',', ',', 'o'),
  ('Businessmen', 'NNS', 'o'),
  ('and', 'CC', 'o'),
  ('other', 'JJ', 'o'),
  ('salaried', 'JJ', 'o'),
  ('classes', 'NNS', 'o'),
  ('who', 'WP', 'o'),
  ('are', 'VBP', 'o'),
  ('Income', 'NNP', 'o'),
  ('Tax', 'NNP', 'o'),
  ('ass

In [0]:
getter.get_next()

[('30', 'CD', 'o'),
 ('P.M', 'NNP', 'o'),
 ('National', 'NNP', 'o'),
 ('Savings', 'NNP', 'o'),
 ('Certificates', 'NNS', 'o'),
 ('(', '(', 'o'),
 ('NSC', 'NNP', 'o'),
 (')', 'SYM', 'o')]

In [0]:
sentences = getter.sentences

In [0]:
cleaned_sentences = copy.deepcopy(sentences)
for outer_index in range(len(sentences)):
  for inner_index in range(len(sentences[outer_index])):
    if type(sentences[outer_index][inner_index][0]) is not str:
      print(sentences[outer_index])
      print(sentences[outer_index][inner_index])
      temp_list = list(sentences[outer_index][inner_index])
      temp_list[0] = ''
      cleaned_sentences[outer_index][inner_index] = tuple(temp_list)
      print("After cleaning : ")
      print(cleaned_sentences[outer_index])
      print(cleaned_sentences[outer_index][inner_index])

[('39', 'CD', 'o'), ('in', 'IN', 'o'), (')', 'SYM', 'o'), ('per', 'IN', 'o'), ('hour', 'NN', 'o'), ('[', '(', 'o'), ('95', 'CD', 'o'), (']', ')', 'o'), ('[', '(', 'o'), ('96', 'CD', 'o'), (']', ')', 'o'), ('*', 'SYM', 'o'), ('Heavy', 'NNP', 'o'), ('rain', 'NN', 'o'), ('â\x80\x94', 'NN', 'o'), ('when', 'WRB', 'o'), ('the', 'DT', 'o'), ('precipitation', 'NN', 'o'), ('rate', 'NN', 'o'), ('is', 'VBZ', 'o'), (nan, 'SYM', 'o'), ('7', 'CD', 'o'), ('.', '.', 'o')]
(nan, 'SYM', 'o')
After cleaning : 
[('39', 'CD', 'o'), ('in', 'IN', 'o'), (')', 'SYM', 'o'), ('per', 'IN', 'o'), ('hour', 'NN', 'o'), ('[', '(', 'o'), ('95', 'CD', 'o'), (']', ')', 'o'), ('[', '(', 'o'), ('96', 'CD', 'o'), (']', ')', 'o'), ('*', 'SYM', 'o'), ('Heavy', 'NNP', 'o'), ('rain', 'NN', 'o'), ('â\x80\x94', 'NN', 'o'), ('when', 'WRB', 'o'), ('the', 'DT', 'o'), ('precipitation', 'NN', 'o'), ('rate', 'NN', 'o'), ('is', 'VBZ', 'o'), ('', 'SYM', 'o'), ('7', 'CD', 'o'), ('.', '.', 'o')]
('', 'SYM', 'o')
[('0', 'CD', 'o'), ('in', 

In [0]:
for outer_index in range(len(sentences)):
  for inner_index in range(len(sentences[outer_index])):
    if type(sentences[outer_index][inner_index][1]) is not str:
      print(sentences[outer_index])
      print(sentences[outer_index][inner_index])
      temp_list = list(sentences[outer_index][inner_index])
      temp_list[1] = ''
      cleaned_sentences[outer_index][inner_index] = tuple(temp_list)
      print("After cleaning : ")
      print(cleaned_sentences[outer_index])
      print(cleaned_sentences[outer_index][inner_index])

[('*', 'SYM', 'o'), ('Source', 'NN', 'o'), (':', ':', 'o'), ('mitbbs.com', 'NNP', 'B-ORG'), ('BBS', 'NNP', 'I-ORG'), (',', ',', 'o'), ('http:', nan, 'o'), ('-LSB-', 'JJ', 'o'), ('FROM', 'IN', 'o'), (':', ':', 'o'), ('69.15.', 'CD', 'B-NUM'), ('-RSB-', 'JJ', 'o')]
('http:', nan, 'o')
After cleaning : 
[('*', 'SYM', 'o'), ('Source', 'NN', 'o'), (':', ':', 'o'), ('mitbbs.com', 'NNP', 'B-ORG'), ('BBS', 'NNP', 'I-ORG'), (',', ',', 'o'), ('http:', '', 'o'), ('-LSB-', 'JJ', 'o'), ('FROM', 'IN', 'o'), (':', ':', 'o'), ('69.15.', 'CD', 'B-NUM'), ('-RSB-', 'JJ', 'o')]
('http:', '', 'o')
[('It', 'PRP', 'o'), ('is', 'VBZ', 'o'), ('also', 'RB', 'o'), ('known', 'VBN', 'o'), ('as', 'IN', 'o'), ('the', 'DT', 'o'), ('bachelor', 'NN', 'o'), ('of', 'IN', 'o'), ('veterinary', 'JJ', 'o'), ('medicine', 'NN', 'o'), ('and', 'CC', 'o'), ('surgery', 'NN', 'o'), ('at', 'IN', 'o'), ('some', 'DT', 'o'), ('universities', 'NNS', 'o'), (';', ':', 'o'), ('BVSc', 'NNP', 'o'), (',', ',', 'o'), ('BVMS', nan, 'o'), (',', 

In [0]:
cleaned_words = []
for sent in cleaned_sentences:
  for word in sent:
    cleaned_words.append(word[0])

In [0]:
#cleaned_words.sort()

In [0]:
cleaned_words[::-1]

['.',
 'demonstrations',
 'anti-government',
 ',',
 'post-election',
 'during',
 'forces',
 'security',
 'with',
 'clashes',
 'in',
 'detained',
 'were',
 'people',
 'of',
 'hundreds',
 'said',
 'groups',
 'rights',
 ',',
 'elections',
 '12',
 'June',
 'disputed',
 "'s",
 'Iran',
 'Following',
 '.',
 'States',
 'United',
 'the',
 'in',
 'eavesdrop',
 'to',
 'Agency',
 'Security',
 'National',
 'the',
 'authorized',
 'secretly',
 'he',
 'confirmed',
 'week',
 'last',
 'Bush',
 'President',
 '.',
 'States',
 'United',
 'the',
 'inside',
 'powers',
 'those',
 'use',
 'to',
 'request',
 'House',
 'White',
 'a',
 'down',
 'turned',
 'specifically',
 'but',
 ',',
 'Qaida',
 'al',
 'pursue',
 'to',
 'powers',
 'extra',
 'president',
 'the',
 'granted',
 'lawmakers',
 'says',
 'Daschle',
 'Mr.',
 ',',
 'Friday',
 'Post',
 'Washington',
 'the',
 'in',
 'piece',
 'opinion',
 'an',
 'In',
 '.',
 'attacks',
 'terror',
 '2001',
 ',',
 '11',
 'September',
 'the',
 'after',
 'al-Qaida',
 'against',
 

In [0]:
len(cleaned_words)

627330

In [0]:
tags = list(set(data["final_tag"].values))
n_tags = len(tags); n_tags


17

In [0]:
#tags.sort()

In [0]:
max_len = 50
word2idx = {w: i for i, w in enumerate(cleaned_words)}
tag2idx = {t: i for i, t in enumerate(tags)}

In [0]:
tag2idx

{'B-ART': 1,
 'B-DT': 15,
 'B-EVE': 11,
 'B-GPE': 12,
 'B-LOC': 16,
 'B-NUM': 0,
 'B-ORG': 9,
 'B-PER': 5,
 'I-ART': 4,
 'I-DT': 6,
 'I-EVE': 2,
 'I-GPE': 3,
 'I-LOC': 8,
 'I-NUM': 7,
 'I-ORG': 10,
 'I-PER': 14,
 'o': 13}

In [0]:
from keras.preprocessing.sequence import pad_sequences
X = [[word2idx[w[0]] for w in s] for s in cleaned_sentences]

In [0]:
X[0]

[214142,
 599971,
 214144,
 621852,
 607551,
 607551,
 134295,
 607551,
 134297,
 539799,
 621852,
 623717,
 627329]

In [0]:
X = pad_sequences(maxlen=max_len, sequences=X, padding="post", value=n_words - 1)


In [0]:
y = [[tag2idx[w[2]] for w in s] for s in cleaned_sentences]


In [0]:
for tag in y:
  print(tag)

[13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13]
[13, 13, 13, 13, 13, 13, 13, 13]
[13, 13, 13]
[13, 13, 13, 13, 13, 5, 14, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 0, 7, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13]
[13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 0, 13, 13, 13, 13, 13, 13, 13, 13]
[13, 13]
[13, 13, 13, 0, 7, 13]
[13, 13, 0, 13, 13]
[13, 13, 13]
[13, 13, 13, 13, 13, 13, 13, 0, 7, 13, 13, 13, 13, 0, 7, 13]
[13, 13, 0, 13, 13, 13, 0, 7, 13, 13, 13, 13, 13, 13, 13, 13, 13, 0, 7, 13, 13, 13, 0, 13, 13, 13, 0, 13, 13, 13, 0, 13, 13, 13, 0, 7, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 13]
[13, 13, 13, 13, 13, 13, 13, 13, 13, 13, 0, 13, 13, 13, 13, 13, 13, 13, 13]
[13, 13]
[15, 13, 13, 0, 7, 13]
[13, 13, 0, 13, 13]
[13, 1

In [0]:
y = pad_sequences(maxlen=max_len, sequences=y, padding="post", value=tag2idx["o"])

In [0]:
count = 0
for tag in y:
  if np.count_nonzero(tag == tag2idx["o"]) == len(tag):
    count += 1
print(count)

2946


In [0]:
len(y)

25427

In [0]:
# So about 3k out of 8500+ sentences are just filled with o's, in other words they aren't that useful(?)..Not anymore..but we can remove the 3k sentences..

In [0]:
from keras.utils import to_categorical
y = [to_categorical(i, num_classes=n_tags) for i in y]

In [0]:
from sklearn.model_selection import train_test_split


In [0]:
X_tr, X_te, y_tr, y_te = train_test_split(X, y, test_size=0.1)


In [0]:
X_tr

array([[626225, 456481, 165753, ..., 627329, 627329, 627329],
       [627082, 626307, 627178, ..., 627329, 627329, 627329],
       [623171, 627296, 627299, ..., 627329, 627329, 627329],
       ...,
       [593508, 625296, 578529, ..., 627329, 627329, 627329],
       [627082, 619979, 624890, ..., 627329, 627329, 627329],
       [611541, 626231, 571656, ..., 627329, 627329, 627329]], dtype=int32)

In [0]:
from keras.models import Model, Input
from keras.layers import LSTM, Embedding, Dense, TimeDistributed, Dropout, Bidirectional

In [0]:
input = Input(shape=(max_len,))
model = Embedding(input_dim=n_words, output_dim=50, input_length=max_len)(input)
model = Dropout(0.1)(model)
model = Bidirectional(LSTM(units=100, return_sequences=True, recurrent_dropout=0.1))(model)
out = TimeDistributed(Dense(n_tags, activation="softmax"))(model)  # softmax output layer


In [0]:
model = Model(input, out)


In [0]:
import keras.backend as K

def f1_score(y_true, y_pred):

    # Count positive samples.
    c1 = K.sum(K.round(K.clip(y_true * y_pred, 0, 1)))
    c2 = K.sum(K.round(K.clip(y_pred, 0, 1)))
    c3 = K.sum(K.round(K.clip(y_true, 0, 1)))

    # If there are no true samples, fix the F1 score at 0.
    if c3 == 0:
        return 0

    # How many selected items are relevant?
    precision = c1 / c2

    # How many relevant items are selected?
    recall = c1 / c3

    # Calculate f1_score
    f1_score = 2 * (precision * recall) / (precision + recall)
    return f1_score


In [0]:
model.compile(optimizer="rmsprop", loss="categorical_crossentropy", metrics=["accuracy"])


In [0]:
history = model.fit(X_tr, np.array(y_tr), batch_size=32, epochs=3, validation_split=0.1, verbose=1)


Train on 20595 samples, validate on 2289 samples
Epoch 1/3
20595/20595 [==============================] - 291s 14ms/step - loss: 0.0757 - acc: 0.9775 - val_loss: 0.0951 - val_acc: 0.9718
Epoch 2/3
20595/20595 [==============================] - 289s 14ms/step - loss: 0.0709 - acc: 0.9790 - val_loss: 0.0934 - val_acc: 0.9725
Epoch 3/3
20595/20595 [==============================] - 290s 14ms/step - loss: 0.0665 - acc: 0.9800 - val_loss: 0.0944 - val_acc: 0.9722


In [0]:
i = 201
p = model.predict(np.array([X_te[i]]))
p = np.argmax(p, axis=-1)
print("{:15} ({:5}): {}".format("Word", "True", "Pred"))
for w, pred in zip(X_te[i], p[0]):
    print("{:15}: {}".format(words[w], tags[pred]))

Word            (True ): Pred
Dhoni          : B-PER
had            : o
few            : o
batting        : o
opportunities  : o
in             : o
the            : o
first          : o
two            : B-NUM
games          : o
of             : o
the            : o
Sri            : B-PER
Lankan         : I-PER
bilateral      : o
ODI            : o
series         : o
(              : o
OctoberâNovember: o
2005           : B-DT
)              : o
and            : o
was            : o
promoted       : o
to             : o
No.            : o
3              : o
in             : o
the            : o
third          : o
ODI            : o
at             : o
Sawai          : B-PER
Mansingh       : I-PER
Stadium        : I-PER
(              : o
Jaipur         : B-LOC
)              : o
.              : o
.              : o
.              : o
.              : o
.              : o
.              : o
.              : o
.              : o
.              : o
.              : o
.              : o
.

In [0]:
!pip install seqeval

In [0]:
from seqeval.metrics import precision_score, recall_score, f1_score, classification_report


In [0]:
test_pred = model.predict(X_te, verbose=1)


2543/2543 [==============================] - 2s 813us/step


In [0]:
idx2tag = {i: w for w, i in tag2idx.items()}

def pred2label(pred):
    out = []
    for pred_i in pred:
        out_i = []
        for p in pred_i:
            p_i = np.argmax(p)
            out_i.append(idx2tag[p_i].replace("PAD", "O"))
        out.append(out_i)
    return out
    
pred_labels = pred2label(test_pred)
test_labels = pred2label(y_te)

In [0]:
print("F1-score: {:.1%}".format(f1_score(test_labels, pred_labels)))


F1-score: 77.5%


In [0]:
print(classification_report(test_labels, pred_labels))


             precision    recall  f1-score   support

          o       0.81      0.80      0.81      8580
        ORG       0.55      0.60      0.57      1116
         DT       0.82      0.78      0.80      1250
        GPE       0.93      0.80      0.86      1061
        LOC       0.77      0.84      0.81      1984
        PER       0.69      0.74      0.72      1482
        NUM       0.49      0.35      0.41       262
        EVE       0.31      0.23      0.27        65
        ART       0.33      0.02      0.04        52

avg / total       0.78      0.77      0.77     15852



In [0]:
test_sentence = ["Hawking", "was", "a", "Fellow", "of", "the", "Royal", "Society", ",", "a", "lifetime", "member",
                 "of", "the", "Pontifical", "Academy", "of", "Sciences", ",", "and", "a", "recipient", "of",
                 "the", "Presidential", "Medal", "of", "Freedom", ",", "the", "highest", "civilian", "award",
                 "in", "the", "United", "States", "."]

In [0]:
x_test_sent = pad_sequences(sequences=[[word2idx.get(w, 0) for w in test_sentence]],
                            padding="post", value=0, maxlen=max_len)

In [0]:
p = model.predict(np.array([x_test_sent[0]]))
p = np.argmax(p, axis=-1)
print("{:15}||{}".format("Word", "Prediction"))
print(30 * "=")
for w, pred in zip(test_sentence, p[0]):
    print("{:15}: {:5}".format(w, tags[pred]))

Word           ||Prediction
Hawking        : B-PER
was            : o    
a              : o    
Fellow         : o    
of             : o    
the            : o    
Royal          : B-ORG
Society        : I-ORG
,              : o    
a              : o    
lifetime       : o    
member         : o    
of             : o    
the            : o    
Pontifical     : o    
Academy        : o    
of             : o    
Sciences       : o    
,              : o    
and            : o    
a              : o    
recipient      : o    
of             : o    
the            : o    
Presidential   : o    
Medal          : o    
of             : o    
Freedom        : o    
,              : o    
the            : o    
highest        : o    
civilian       : o    
award          : o    
in             : o    
the            : o    
United         : B-LOC
States         : I-LOC
.              : o    


In [0]:
word2idx["Stalin"]

613711

In [0]:
model.save('ner_model-v2.h5')

In [0]:
!pwd

/content


In [0]:
np.save('word2idx.npy', word2idx)

In [0]:
np.save('tag2idx.npy', tag2idx)

In [0]:
t2i = np.load('tag2idx.npy')

In [0]:
t2i

array({'B-NUM': 0, 'B-ART': 1, 'I-EVE': 2, 'I-GPE': 3, 'I-ART': 4, 'B-PER': 5, 'I-DT': 6, 'I-NUM': 7, 'I-LOC': 8, 'B-ORG': 9, 'I-ORG': 10, 'B-EVE': 11, 'B-GPE': 12, 'o': 13, 'I-PER': 14, 'B-DT': 15, 'B-LOC': 16},
      dtype=object)

In [0]:
w2i = np.load('word2idx.npy')

In [0]:
w2i = dict(enumerate(w2i.flatten()))[0]

In [0]:
i2t = {i:w for w, i in dict(t2i).items()}

TypeError: ignored

In [0]:
i2t = {i:w for w,i in dict(enumerate(t2i.flatten(), 1))[1].items()}

In [0]:
i2t

{0: 'B-NUM',
 1: 'B-ART',
 2: 'I-EVE',
 3: 'I-GPE',
 4: 'I-ART',
 5: 'B-PER',
 6: 'I-DT',
 7: 'I-NUM',
 8: 'I-LOC',
 9: 'B-ORG',
 10: 'I-ORG',
 11: 'B-EVE',
 12: 'B-GPE',
 13: 'o',
 14: 'I-PER',
 15: 'B-DT',
 16: 'B-LOC'}

In [0]:
from keras.models import load_model
loaded_model = load_model('ner_model-v2.h5')

In [0]:
test_sentence = ["Hawking", "was", "a", "Fellow", "of", "the", "Royal", "Society", ",", "a", "lifetime", "member",
                 "of", "the", "Pontifical", "Academy", "of", "Sciences", ",", "and", "a", "recipient", "of",
                 "the", "Presidential", "Medal", "of", "Freedom", ",", "the", "highest", "civilian", "award",
                 "in", "the", "United", "States", "."]


In [0]:
x_test_sent = pad_sequences(sequences=[[w2i.get(w, 0) for w in test_sentence]],
                            padding="post", value=0, maxlen=max_len)

In [0]:
p = loaded_model.predict(np.array([x_test_sent[0]]))
p = np.argmax(p, axis=-1)
print("{:15}||{}".format("Word", "Prediction"))
print(30 * "=")
for w, pred in zip(test_sentence, p[0]):
    print("{:15}: {:5}".format(w, i2t[pred]))

Word           ||Prediction
Hawking        : B-PER
was            : o    
a              : o    
Fellow         : o    
of             : o    
the            : o    
Royal          : B-ORG
Society        : I-ORG
,              : o    
a              : o    
lifetime       : o    
member         : o    
of             : o    
the            : o    
Pontifical     : o    
Academy        : o    
of             : o    
Sciences       : o    
,              : o    
and            : o    
a              : o    
recipient      : o    
of             : o    
the            : o    
Presidential   : o    
Medal          : o    
of             : o    
Freedom        : o    
,              : o    
the            : o    
highest        : o    
civilian       : o    
award          : o    
in             : o    
the            : o    
United         : B-LOC
States         : I-LOC
.              : o    
